# Capstone Project - The Battle of Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal suburb for a supermarket. This report will be targeted to stakeholders interested in opening an **Asian supermarket** in **Melbourne**, the capital city of the State of Victoria in Australia.

According to a [news report](https://www.abc.net.au/news/2019-05-03/supermarket-market-share-roy-morgan-single-source/11073926?nw=0), the supermarket scene in Australia is very much dominated by two supermarket chains - Woolworths and Coles. In 2018, the two together had more than 60% market share. The remaining market share was shared among Aldi, IGA and other supermarkets. These supermarket chains often sell similar varieties of products and compete at prices, which is a strategy difficult for new market entrants to follow. However, if a supermarket can differentiate itself with a different range of products, it may be able to compete with those supermarket chains.

According to the [2016 Census](https://en.wikipedia.org/wiki/Asian_Australians#cite_note-guest.censusdata.abs.gov.au-2), 16.3% of the Australian population had Asian ancestry. In Melbourne, 24.4% of the population had Asian ancestry. Therefore there is a market for Asian grocery. This project will look for a suburb to open an Asian supermarket to cater for this market.

In particular, we will look for such a suburb with these criteria:
* the suburb has a **high population**
* the suburb has a **low supermarket to population ratio**
* the suburb has a **high proportion of population with Asian ancestry**

## Data <a name="data"></a>

In this project, we will use suburbs to define our neighborhoods. In Australia, decisions about names and boundaries of suburbs are made by local councils, then approved by State governments.

Based on the criteria set out to tackle our business problem, the following data sources will be used to generate required information:
* suburb boundaries data of Victoria in the format of GeoJSON, produced by **Department of Industry, Science, Energy and Resources**, available at [**data.gov.au**](https://data.gov.au/)
* locations of existing supermarkets, obtained by using **Foursquare API**
* 2016 Census data, produced by **Australian Bureau of Statistics**

### Suburb Boundaries
In this section, we will produce a list of suburbs which are within 5 km of the Melbourne city centre. We will then compute latitude & longitude coordinates of centroid for each suburb, based on its boundary. After that, we will visualise these suburbs with their centroids on map.

We will first obtain latitude & longitude coordinates of Melbourne city centre, using geopy library.

In [1]:
!pip install geopy
from geopy.geocoders import Nominatim

In [2]:
address = 'Melbourne, VIC'

geolocator = Nominatim(user_agent="vic_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
melbourne_city_centre = (latitude, longitude)
print('The geographical coordinates of Melbourne are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Melbourne are -37.8142176, 144.9631608.


We will now retrieve and load the GeoJSON file of Victoria's suburb boundaries from **data.gov.au**.

In [3]:
import requests
import json

url = 'https://data.gov.au/geoserver/vic-suburb-locality-boundaries-psma-administrative-boundaries/wfs?request=GetFeature&typeName=ckan_af33dd8c_0534_4e18_9245_fc64440f742e&outputFormat=json'
response = requests.get(url)
vic_suburbs = json.loads(response.text)

Let's take a look at the contents of GeoJSON file.

In [4]:
vic_suburbs['features'][0]

{'type': 'Feature',
 'id': 'ckan_af33dd8c_0534_4e18_9245_fc64440f742e.1',
 'geometry': {'type': 'MultiPolygon',
  'coordinates': [[[[141.74552399, -35.07228701],
     [141.74552471, -35.07201624],
     [141.74748471, -35.06367123],
     [141.74909525, -35.05681288],
     [141.74917403, -35.05647197],
     [141.75887404, -35.05225699],
     [141.77005396, -35.04914101],
     [141.77057401, -35.04899703],
     [141.76823304, -35.04349501],
     [141.76757096, -35.04270197],
     [141.76709398, -35.03982199],
     [141.76544215, -35.03808514],
     [141.76547768, -35.03782986],
     [141.76408494, -35.03523684],
     [141.76398063, -35.03505673],
     [141.76387633, -35.03487661],
     [141.75923139, -35.02629546],
     [141.77479178, -35.02631526],
     [141.77477947, -35.02789069],
     [141.79121543, -35.02632192],
     [141.79143466, -35.02629765],
     [141.79143596, -35.04874003],
     [141.79351097, -35.04729598],
     [141.79428796, -35.04709498],
     [141.79636183, -35.04970131]

So each item in **'features'** contains geographical information of a suburb. **'coordinates'** draw the boundary of the suburb. **'vic_loca_2'** contains the name of the suburb. In the above example, the suburb's name is UNDERBOOL.

Let's check how many suburbs there are in Victoria.

In [5]:
len(vic_suburbs['features'])

2973

We will now filter out all suburbs which are outside the 5 km radius from Melbourne city centre.

In [6]:
from geopy.distance import lonlat, distance

# Define a function which check if any coordinate of the boundary of a suburb is within 5 km from Melbourne city centre
def keep(feature):
    for coordinate in feature['geometry']['coordinates'][0][0]:
        if distance(melbourne_city_centre, lonlat(*coordinate)).km <= 5:
            return True

# Filter and keep all suburbs which are within 5 km of Melbourne city centre, then turn them into a list
filtered_features = list(filter(keep, vic_suburbs['features']))

print('{} suburbs are within 5 km of Melbourne city centre:'.format(len(filtered_features)))

for feature in filtered_features:
    print(feature['properties']['vic_loca_2'])

41 suburbs are within 5 km of Melbourne city centre:
BURNLEY
WINDSOR
PRINCES HILL
DOCKLANDS
CLIFTON HILL
RICHMOND
NORTH MELBOURNE
FOOTSCRAY
FITZROY
COLLINGWOOD
MELBOURNE
ABBOTSFORD
FITZROY NORTH
HAWTHORN
SOUTH WHARF
WEST MELBOURNE
EAST MELBOURNE
PARKVILLE
PORT MELBOURNE
TRAVANCORE
KENSINGTON
ASCOT VALE
CARLTON NORTH
CARLTON
TOORAK
SOUTH MELBOURNE
KEW
SOUTHBANK
BRUNSWICK EAST
CREMORNE
BRUNSWICK
NORTHCOTE
FAIRFIELD
SOUTH YARRA
ALBERT PARK
ST KILDA
FLEMINGTON
PRAHRAN
BRUNSWICK WEST
MIDDLE PARK
ST KILDA WEST


As the original GeoJSON file containing all Victoria's suburbs is large, we will re-compile a new GeoJSON file with only the filtered suburbs.

In [7]:
suburbs_within_5km = {'type': 'FeatureCollection', 'features': []}
suburbs_within_5km['features'] = filtered_features

We will now compute a list of centroids of these 41 suburbs. These centroids will be used to search for nearby supermarkets in the section of **Foursquare**.

In [8]:
!pip install shapely
from shapely.geometry import shape

In [9]:
suburb_centroids = []

for feature in filtered_features:
    boundary = shape(feature["geometry"])
    suburb_centroids.append(boundary.centroid)

Let's visualise boundaries of these 41 suburbs, their centroids, and Melbourne city centre on map.

In [10]:
!pip install folium==0.11.0
import folium

In [11]:
# Create map of Melbourne
map_suburbs_within_5km = folium.Map(location=melbourne_city_centre, tiles='cartodbpositron', zoom_start=12)

# Add city centre marker to map
folium.Marker(location=melbourne_city_centre, tooltip=melbourne_city_centre).add_to(map_suburbs_within_5km)

# Add markers of suburb centroids to map
for centroid in suburb_centroids:
    folium.CircleMarker(location=[centroid.y, centroid.x], radius=5, color='blue', fill=True, fill_color='#3186cc', fill_opacity=0.7, parse_html=True).add_to(map_suburbs_within_5km)

# Add suburb boundaries to map
folium.GeoJson(suburbs_within_5km, name='suburb_boundary', tooltip=folium.GeoJsonTooltip(['vic_loca_2'], labels=False)).add_to(map_suburbs_within_5km)

map_suburbs_within_5km

### Foursquare
Now that we have centroids of the 41 suburbs. In this section, we will use Foursquare API to get info on supermarkets in each suburb.

Foursquare credentials are defined in hidden cell below.

In [12]:
# The code was removed by Watson Studio for sharing.

We will now search for supermarkets nearby centroids of the 41 suburbs. Let's first look at Melbourne city centre as an example.

In [13]:
!pip install pandas==1.0.4

In [14]:
import pandas as pd
from pandas import json_normalize

supermarket_category = '52f2ab2ebcbc57f1066b8b46' # Supermarket's category ID was taken from Foursquare web site
radius = 2000
LIMIT = 50

url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&categoryId={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT, supermarket_category)
results = requests.get(url).json()
items = results['response']['venues']

# Transform contents of the JSON into a dataframe
df_foursquare = json_normalize(items)
df_foursquare.head()

id                       name  \
0  55f76d71498e11ecf6921ecd  Woolworths Metro Swanston   
1  5681d74c498e9e6f447639b5           Woolworths Metro   
2  55e6ccbc498efc941443b8a9      TANG - The Asian Food   
3  4b7fbe7bf964a520d33b30e3                      Coles   
4  4b058750f964a520728b22e3                      Coles   

                                          categories    referralId  hasPerk  \
0  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   
1  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   
2  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   
3  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   
4  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   

     location.address  location.lat  location.lng  \
0     160 Swanston St    -37.813828    144.965938   
1     60 Elizabeth St    -37.816746    144.964368   
2  185 Russell Street    -37.811935    144.967726   
3      201 Spencer St    -37.814913    144.952310   
4     26 Elizabeth St    -37.817720    144.964749   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': -37.813828, 'lng'...                248   
1  [{'label': 'display', 'lat': -37.8167460293124...                300   
2  [{'label': 'display', 'lat': -37.8119351687113...                475   
3  [{'label': 'display', 'lat': -37.8149132677007...                957   
4  [{'label': 'display', 'lat': -37.8177199095187...                414   

  location.postalCode location.cc          location.neighborhood  \
0                3000          AU  Melbourne CBD, Melbourne, VIC   
1                3000          AU                            NaN   
2                3000          AU                  Melbourne CBD   
3                3008          AU                 Docklands, VIC   
4                3000          AU                            NaN   

   location.city location.state location.country  \
0      Melbourne            VIC        Australia   
1  Melbourne CBD            VIC        Australia   
2      Melbourne            VIC        Australia   
3      Docklands            VIC        Australia   
4      Melbourne            VIC        Australia   

                           location.formattedAddress  \
0   [160 Swanston St, Melbourne VIC 3000, Australia]   
1  [60 Elizabeth St, Melbourne CBD VIC 3000, Aust...   
2  [185 Russell Street (Little Bourke St), Melbou...   
3    [201 Spencer St, Docklands VIC 3008, Australia]   
4  [26 Elizabeth St (Btwn Flinders St & Flinders ...   

             location.crossStreet  
0                             NaN  
1                             NaN  
2                Little Bourke St  
3                             NaN  
4  Btwn Flinders St & Flinders Ln

In [15]:
df_foursquare.shape

(40, 18)

It can be seen that within 2 km radius of Melbourne city centre, there are 40 supermarkets. Because the limit of number of results returned from Foursquare for each search is 50, it is useful to check if the results we get have reached the limit. If the limit is reached, it means potentially some supermarkets are not returned in the results. In that case, we will need to lower the radius, so that the search will cover a smalled area.

We will now continue to do the search with Foursquare API on the 41 centroids and combine them into one dataframe.

In [16]:
for centroid in suburb_centroids:
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&categoryId={}'.format(
        CLIENT_ID, CLIENT_SECRET, centroid.y, centroid.x, VERSION, radius, LIMIT, supermarket_category)
    results = requests.get(url).json()
    items = results['response']['venues']
    print('Limit reached:', len(items)) if len(items) >= 50 else None # Check if the number of results reaches the limit
    df_foursquare = df_foursquare.append(json_normalize(items), ignore_index=True)

df_foursquare.shape

(740, 18)

The dataframe contains 740 supermarkets. However, it should be noted that some of them are duplicates of the same supermarkets. This is because we are using a radius of 2 km for each centroid, so there are covered areas overlapped with each other.

Let's sort the dataframe by column **'id'** and we can see the duplicates.

In [17]:
df_foursquare.sort_values(by='id').head(10)

id                               name  \
550  4b058750f964a520728b22e3                              Coles   
539  4b058750f964a520728b22e3                              Coles   
4    4b058750f964a520728b22e3                              Coles   
389  4b058750f964a520728b22e3                              Coles   
231  4b058750f964a520728b22e3                              Coles   
197  4b058750f964a520728b22e3                              Coles   
105  4b058750f964a520728b22e3                              Coles   
486  4b058750f964a520728b22e3                              Coles   
346  4b058750f964a520728b22e3                              Coles   
129  4b058753f964a520198c22e3  Piedimonte's Supermarket & Liquor   

                                            categories    referralId  hasPerk  \
550  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726886    False   
539  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726885    False   
4    [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726877    False   
389  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726883    False   
231  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726881    False   
197  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726880    False   
105  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726879    False   
486  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726885    False   
346  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726882    False   
129  [{'id': '52f2ab2ebcbc57f1066b8b46', 'name': 'S...  v-1591726879    False   

    location.address  location.lat  location.lng  \
550  26 Elizabeth St    -37.817720    144.964749   
539  26 Elizabeth St    -37.817720    144.964749   
4    26 Elizabeth St    -37.817720    144.964749   
389  26 Elizabeth St    -37.817720    144.964749   
231  26 Elizabeth St    -37.817720    144.964749   
197  26 Elizabeth St    -37.817720    144.964749   
105  26 Elizabeth St    -37.817720    144.964749   
486  26 Elizabeth St    -37.817720    144.964749   
346  26 Elizabeth St    -37.817720    144.964749   
129   37-49a Best St    -37.783482    144.983427   

                               location.labeledLatLngs  location.distance  \
550  [{'label': 'display', 'lat': -37.8177199095187...                933   
539  [{'label': 'display', 'lat': -37.8177199095187...               1915   
4    [{'label': 'display', 'lat': -37.8177199095187...                414   
389  [{'label': 'display', 'lat': -37.8177199095187...               1610   
231  [{'label': 'display', 'lat': -37.8177199095187...               1009   
197  [{'label': 'display', 'lat': -37.8177199095187...               2260   
105  [{'label': 'display', 'lat': -37.8177199095187...               2113   
486  [{'label': 'display', 'lat': -37.8177199095187...               1945   
346  [{'label': 'display', 'lat': -37.8177199095187...               1397   
129  [{'label': 'display', 'lat': -37.7834824209649...               1459   

    location.postalCode location.cc location.neighborhood  location.city  \
550                3000          AU                   NaN      Melbourne   
539                3000          AU                   NaN      Melbourne   
4                  3000          AU                   NaN      Melbourne   
389                3000          AU                   NaN      Melbourne   
231                3000          AU                   NaN      Melbourne   
197                3000          AU                   NaN      Melbourne   
105                3000          AU                   NaN      Melbourne   
486                3000          AU                   NaN      Melbourne   
346                3000          AU                   NaN      Melbourne   
129                3068          AU                   NaN  Fitzroy North   

    location.state location.country  \
550            VIC        Australia   
539            VIC        Australia   
4          

We will now drop the duplicates by column **'id'** and check the total number of supermarkets again.

In [18]:
df_foursquare.drop_duplicates(subset='id', inplace=True, ignore_index=True)
df_foursquare.shape

(126, 18)

So there are 126 unique supermarkets from our searches. However, as we use a radius of 2 km in our searches, some of the searches actually cover areas beyond the total areas of 41 suburbs. Therefore we need to check and cleanse our data to ensure these supermarkets are within the boundaries of the 41 suburbs. We will check the supermarkets' coordinates against the suburbs' boundaries.

In [19]:
import numpy as np
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon

# Create an empty column of NaN in the dataframe
df_foursquare['suburb'] = np.nan

# Check every supermarket location against boundary of every 41 suburbs. Fill the empty column with the name of the suburb if the supermarket is within its boundary. 
for i in range(len(df_foursquare)):
    supermarket_location = Point(df_foursquare.loc[i, 'location.lng'], df_foursquare.loc[i, 'location.lat'])
    for j in range(len(suburbs_within_5km['features'])):
        suburb_boundary = Polygon(suburbs_within_5km['features'][j]['geometry']['coordinates'][0][0])
        if suburb_boundary.contains(supermarket_location):
            df_foursquare.loc[i, 'suburb'] = suburbs_within_5km['features'][j]['properties']['vic_loca_2']
            break

# Drop row if it has NaN in the 'suburb' column
df_foursquare.dropna(subset=['suburb'], inplace=True)

# Reset index
df_foursquare.reset_index(drop=True, inplace=True)

df_foursquare.shape

(108, 19)

We now know that there are 108 supermarkets within the boundaries of the 41 suburbs. Let's clean up the dataframe a bit more and remove unnecessary columns.

In [20]:
# Change the values of the categories' column with category names
for i in range(len(df_foursquare['categories'])):
    df_foursquare.loc[i, 'categories'] = df_foursquare.loc[i, 'categories'][0]['name']

# Rename column names
df_foursquare.rename(
    columns={'location.lat': 'lat',
             'location.lng': 'lng',
             'location.postalCode': 'postalCode',
             'location.formattedAddress': 'formattedAddress'},
    inplace=True
)

# Slice the dataframe with only the columns we need
df_foursquare = df_foursquare[['id', 'name', 'categories', 'suburb', 'postalCode', 'lat', 'lng', 'formattedAddress']]

df_foursquare.head()

id                       name   categories  \
0  55f76d71498e11ecf6921ecd  Woolworths Metro Swanston  Supermarket   
1  5681d74c498e9e6f447639b5           Woolworths Metro  Supermarket   
2  55e6ccbc498efc941443b8a9      TANG - The Asian Food  Supermarket   
3  4b7fbe7bf964a520d33b30e3                      Coles  Supermarket   
4  4b058750f964a520728b22e3                      Coles  Supermarket   

      suburb postalCode        lat         lng  \
0  MELBOURNE       3000 -37.813828  144.965938   
1  MELBOURNE       3000 -37.816746  144.964368   
2  MELBOURNE       3000 -37.811935  144.967726   
3  MELBOURNE       3008 -37.814913  144.952310   
4  MELBOURNE       3000 -37.817720  144.964749   

                                    formattedAddress  
0   [160 Swanston St, Melbourne VIC 3000, Australia]  
1  [60 Elizabeth St, Melbourne CBD VIC 3000, Aust...  
2  [185 Russell Street (Little Bourke St), Melbou...  
3    [201 Spencer St, Docklands VIC 3008, Australia]  
4  [26 Elizabeth St (Btwn Flinders St & Flinders ...

### 2016 Census - population data
In this section, we will import population data of the 41 suburbs, produced in the 2016 Census by Australian Bureau of Statistics (ABS).

In [21]:
from zipfile import ZipFile
import shutil

 
url = 'https://www.censusdata.abs.gov.au/CensusOutput/copsubdatapacks.nsf/All%20docs%20by%20catNo/2016_GCP_SSC_for_Vic/$File/2016_GCP_SSC_for_Vic_short-header.zip?OpenElement&key=2cab12d4-cf70-14c9-37c5-c3ee2e138b1d'
response = requests.get(url)

# Download one of the 2016 Census data packages from ABS
with open('2016_GCP_SSC_for_Vic_short-header.zip', 'wb') as fd:
    for chunk in response.iter_content(chunk_size=128):
        fd.write(chunk)

file_name = '2016_GCP_SSC_for_Vic_short-header.zip'

# Extract files from the zip file
with ZipFile(file_name, 'r') as zip:
    zip.extractall(members=('Metadata/Metadata_2016_GCP_DataPack.xlsx', 'Metadata/2016Census_geog_desc_1st_and_2nd_release.xlsx', '2016 Census GCP State Suburbs for VIC/2016Census_G01_VIC_SSC.csv'))

# Move files and remove empty directories
shutil.move('Metadata/Metadata_2016_GCP_DataPack.xlsx', 'Metadata_2016_GCP_DataPack.xlsx')
shutil.move('Metadata/2016Census_geog_desc_1st_and_2nd_release.xlsx', '2016Census_geog_desc_1st_and_2nd_release.xlsx')
shutil.move('2016 Census GCP State Suburbs for VIC/2016Census_G01_VIC_SSC.csv', '2016Census_G01_VIC_SSC.csv')
shutil.rmtree('Metadata')
shutil.rmtree('2016 Census GCP State Suburbs for VIC')

In [22]:
!pip install xlrd
import xlrd

df_metadata = pd.read_excel('Metadata_2016_GCP_DataPack.xlsx', sheet_name='Cell descriptors information', skiprows=10)
df_metadata.head()

Sequential         Short                          Long DataPack file  \
0         G1       Tot_P_M           Total_Persons_Males           G01   
1         G2       Tot_P_F         Total_Persons_Females           G01   
2         G3       Tot_P_P         Total_Persons_Persons           G01   
3         G4  Age_0_4_yr_M    Age_groups_0_4_years_Males           G01   
4         G5  Age_0_4_yr_F  Age_groups_0_4_years_Females           G01   

  Profile table Column heading description in profile  
0          G01a                                 Males  
1          G01a                               Females  
2          G01a                               Persons  
3          G01a                                 Males  
4          G01a                               Females

df_metadata contains info on column labels (in short and long form) of individual tables. 

In [23]:
df_geography = pd.read_excel('2016Census_geog_desc_1st_and_2nd_release.xlsx', sheet_name='2016_ASGS_Non-ABS_Structures')
df_geography.head()

ASGS_Structure Census_Code_2016  ASGS_Code_2016 Census_Name_2016  \
0            AUS              036              36        AUSTRALIA   
1            CED           CED101             101            Banks   
2            CED           CED102             102           Barton   
3            CED           CED103             103        Bennelong   
4            CED           CED104             104          Berowra   

      Area sqkm  
0  7.688126e+06  
1  4.944600e+01  
2  3.964660e+01  
3  5.860520e+01  
4  7.496359e+02

df_geography contains suburb codes and names used in 2016 Census.

In [24]:
df_G01 = pd.read_csv('2016Census_G01_VIC_SSC.csv')
df_G01.head()

SSC_CODE_2016  Tot_P_M  Tot_P_F  Tot_P_P  Age_0_4_yr_M  Age_0_4_yr_F  \
0      SSC20001        0        0        0             0             0   
1      SSC20002     4111     4081     8184           163           157   
2      SSC20003     1904     1994     3897           101            79   
3      SSC20004        0        0        0             0             0   
4      SSC20005       83       88      171             0             0   

   Age_0_4_yr_P  Age_5_14_yr_M  Age_5_14_yr_F  Age_5_14_yr_P  ...  \
0             0              0              0              0  ...   
1           319            165            164            325  ...   
2           179            259            289            550  ...   
3             0              0              0              0  ...   
4             0             17             12             29  ...   

   High_yr_schl_comp_Yr_8_belw_P  High_yr_schl_comp_D_n_g_sch_M  \
0                              0                              0   
1                            169                             25   
2                             89                              6   
3                              0                              0   
4                              8                              0   

   High_yr_schl_comp_D_n_g_sch_F  High_yr_schl_comp_D_n_g_sch_P  \
0                              0                              0   
1                             37                             70   
2                              4                             11   
3                              0                              0   
4                              0                              0   

   Count_psns_occ_priv_dwgs_M  Count_psns_occ_priv_dwgs_F  \
0                           0                           0   
1                        3618                        3627   
2                        1801                        1898   
3                           0                           0   
4                          64                          63   

   Count_psns_occ_priv_dwgs_P  Count_Persons_other_dwgs_M  \
0                           0                           0   
1                        7245                         448   
2                        3701                          75   
3                           0                           0   
4                         127                           7   

   Count_Persons_other_dwgs_F  Count_Persons_other_dwgs_P  
0                           0                           0  
1                         398                         840  
2                          93                         165  
3                           0                           0  
4                           9                          16  

[5 rows x 109 columns]

df_G01 contains demographic of all Victorian suburbs. The column 'SSC_CODE_2016' refers to different suburbs, which is not obvious to us the exact suburbs they are referring to, therefore we will join df_G01 with df_geography to get the suburbs names. Also the column we are intereted in df_G01 is 'Tot_P_P', which is short for 'Total_Persons_Persons' according to df_metadata.

In [25]:
# Rename column 'Tot_P_P'
df_G01.rename(columns={'Tot_P_P': 'Total_Persons_Persons'}, inplace=True)

# Join df_G01 with df_geography
df_G01 = df_G01.join(df_geography[['Census_Code_2016', 'Census_Name_2016']].set_index('Census_Code_2016'), on='SSC_CODE_2016')

# Rearrange and slice the columns we require
df_G01 = df_G01[['SSC_CODE_2016', 'Census_Name_2016', 'Total_Persons_Persons']]
df_G01.head()

SSC_CODE_2016   Census_Name_2016  Total_Persons_Persons
0      SSC20001           Abbeyard                      0
1      SSC20002  Abbotsford (Vic.)                   8184
2      SSC20003         Aberfeldie                   3897
3      SSC20004          Aberfeldy                      0
4      SSC20005            Acheron                    171

In [26]:
df_G01.shape

(2931, 3)

We will now filter df_G01 to keep rows of the 41 suburbs. Let's first create a list of the 41 suburbs.

In [27]:
suburb_list = []

for feature in filtered_features:
    suburb_list.append(feature['properties']['vic_loca_2'])

print(suburb_list)

['BURNLEY', 'WINDSOR', 'PRINCES HILL', 'DOCKLANDS', 'CLIFTON HILL', 'RICHMOND', 'NORTH MELBOURNE', 'FOOTSCRAY', 'FITZROY', 'COLLINGWOOD', 'MELBOURNE', 'ABBOTSFORD', 'FITZROY NORTH', 'HAWTHORN', 'SOUTH WHARF', 'WEST MELBOURNE', 'EAST MELBOURNE', 'PARKVILLE', 'PORT MELBOURNE', 'TRAVANCORE', 'KENSINGTON', 'ASCOT VALE', 'CARLTON NORTH', 'CARLTON', 'TOORAK', 'SOUTH MELBOURNE', 'KEW', 'SOUTHBANK', 'BRUNSWICK EAST', 'CREMORNE', 'BRUNSWICK', 'NORTHCOTE', 'FAIRFIELD', 'SOUTH YARRA', 'ALBERT PARK', 'ST KILDA', 'FLEMINGTON', 'PRAHRAN', 'BRUNSWICK WEST', 'MIDDLE PARK', 'ST KILDA WEST']


Next, we will filter the dataframe to keep the 41 suburbs only.

In [28]:
import re

# Insert empty column 'suburb' into df_G01
df_G01.insert(2, 'suburb', np.nan)

# Put the 41 suburbs in the 'suburb' column
for suburb in suburb_list:
    for i in range(len(df_G01)):
        if suburb == re.sub(' \(.*\)', '', df_G01.loc[i, 'Census_Name_2016']).upper():
            df_G01.loc[i, 'suburb'] = suburb

# Filter the dataframe to keep data only for the 41 suburbs
df_population = df_G01[df_G01['suburb'].notna()]

# Reset index
df_population.reset_index(drop=True, inplace=True)

df_population.head()

SSC_CODE_2016    Census_Name_2016          suburb  Total_Persons_Persons
0      SSC20002   Abbotsford (Vic.)      ABBOTSFORD                   8184
1      SSC20017  Albert Park (Vic.)     ALBERT PARK                   6215
2      SSC20074          Ascot Vale      ASCOT VALE                  14750
3      SSC20359    Brunswick (Vic.)       BRUNSWICK                  24473
4      SSC20360      Brunswick East  BRUNSWICK EAST                  11504

In [29]:
df_population.shape

(41, 4)

So we now have df_population containing population data of the 41 suburbs.

### 2016 Census - ancestry data

In this section, we will import ancestry data of the 41 suburbs. This data was also produced in the 2016 Census by ABS; however, it needs to be generated with the [**TableBuilder**](https://www.abs.gov.au/websitedbs/d3310114.nsf/home/about+tablebuilder) on the ABS website, with a free registered account. Therefore, it has been downloaded from the ABS website in advance and uploaded to cloud storage.

This is how the table looks like in Excel:![alt text](https://cloud-object-storage-fg-cos-standard-xwg.s3.au-syd.cloud-object-storage.appdomain.cloud/ancestry_screenshot.JPG)

First, we will download the file from cloud storage.

In [30]:
url = 'https://cloud-object-storage-fg-cos-standard-xwg.s3.au-syd.cloud-object-storage.appdomain.cloud/ancestry_by_vic_suburbs.xls'
response = requests.get(url)

with open('ancestry_by_vic_suburbs.xls', 'wb') as fd:
    for chunk in response.iter_content(chunk_size=128):
        fd.write(chunk)

We will now import the file as a dataframe.

In [31]:
df_ancestry = pd.read_excel('ancestry_by_vic_suburbs.xls', header=[8, 9], skiprows=[10], skipfooter=7)
df_ancestry.drop(columns=('ANC1P - 1 Digit Level', 'ANC2P - 1 Digit Level'), inplace=True) #Drop first column which is of empty values
df_ancestry.rename(columns={'ANC1P - 1 Digit Level': 'SSC (UR)', 'ANC2P - 1 Digit Level.1': ''}, inplace=True) # Rename first column

with pd.option_context('display.max_columns', 133):
    display(df_ancestry.head())

SSC (UR) Oceanian                      \
                     Oceanian North-West European   
0           Abbeyard        0                   0   
1  Abbotsford (Vic.)       21                  58   
2         Aberfeldie        4                  33   
3          Aberfeldy        0                   0   
4            Acheron        0                   4   

                                                                  \
  Southern and Eastern European North African and Middle Eastern   
0                             0                                0   
1                            66                               15   
2                            77                                8   
3                             0                                0   
4                             0                                0   

                                                                \
  South-East Asian North-East Asian Southern and Central Asian   
0                0                0                          0   
1               36                3                         27   
2                3                3                         10   
3                0                0                          0   
4                0                0                          0   

                                                                   \
  Peoples of the Americas Sub-Saharan African Supplementary codes   
0                       0                   0                   0   
1                      25                   7                   3   
2                       9                   4                   0   
3                       0                   0                   0   
4                       0                   0                   0   

                 North-West European                      \
  Not applicable            Oceanian North-West European   
0              0                   0                   0   
1            920                 662                1326   
2            561                 303                 471   
3              0                   0                   0   
4             39                  20                  31   

                                                                  \
  Southern and Eastern European North African and Middle Eastern   
0                             0                                0   
1                           201                               14   
2                           149                                3   
3                             0                                0   
4                             3                                0   

                                                                \
  South-East Asian North-East Asian Southern and Central Asian   
0                0                0                          0   
1               31               49                         16   
2                5               15                         14   
3                0                0                          0   
4                0                0                          0   

                                                                   \
  Peoples of the Americas Sub-Saharan African Supplementary codes   
0                       0                   0                   0   
1                      25                  19                   9   
2                       3                  16                   0   
3                       0                   0                   0   
4                       0                   0                   0   

                 Southern and Eastern European                      \
  Not applicable                      Oceanian North-West European   
0              0                             0                   0   
1           1260                            51                  30   
2            573                            61                  20   
3              0     

In [32]:
df_ancestry.shape

(2932, 133)

There are 133 columns in the dataframe. It is worth explaining what these columns stand for. The first column 'SSC (UR)' is the suburbs of Victoria. From the second column and beyond, they stand for the response from individuals regarding their ancestry. In the Census, individuals were asked about their ancestry and they could provide up to two responses. For example, one could provide the first response as Oceanian and the second response North-West European. This can possibly mean the individual's one parent from Oceanian ancestry and the other parent from North-West European. An individual could also choose to provide one response only; or not to provide any response at all, which would then be counted as 'Not stated'.

Let's take a look at the column labels.

In [33]:
print(df_ancestry.columns.get_level_values(0).unique())
print(df_ancestry.columns.get_level_values(1).unique())

Index(['SSC (UR)', 'Oceanian', 'North-West European',
       'Southern and Eastern European', 'North African and Middle Eastern',
       'South-East Asian', 'North-East Asian', 'Southern and Central Asian',
       'Peoples of the Americas', 'Sub-Saharan African', 'Supplementary codes',
       'Not stated', 'Total'],
      dtype='object')
Index(['', 'Oceanian', 'North-West European', 'Southern and Eastern European',
       'North African and Middle Eastern', 'South-East Asian',
       'North-East Asian', 'Southern and Central Asian',
       'Peoples of the Americas', 'Sub-Saharan African', 'Supplementary codes',
       'Not applicable'],
      dtype='object')


The responses were categorised in 9 regions:
* Oceanian
* North-West European
* Southern and Eastern European
* North African and Middle Eastern
* South-East Asian
* North-East Asian
* Southern and Central Asian
* Peoples of the Americas
* Sub-Saharan African

For our project, we consider **South-East Asian**, **North-East Asian**, and **Southern and Central Asian** as Asian. We want to know the proportion of population with Asian ancestry in the 41 suburbs. So population who provided Asian ancestry in either 1st or 2nd response, or in both responses are considered Asian for our purpose.

We will process df_ancestry to extract this information in the following.

In [34]:
idx = pd.IndexSlice

# Create a new column which sums the number of people who gave Asian ancestry in their first response
df_ancestry['asian_1st_response'] = df_ancestry.loc[idx[:], idx[['South-East Asian', 'North-East Asian', 'Southern and Central Asian']]].sum(axis=1)

# Create a new column which sums the number of people who gave Asian ancestry in their second response, but not in their first response
df_ancestry['asian_2nd_response'] = df_ancestry.loc[idx[:], idx[
    ['Oceanian',
     'North-West European',
     'Southern and Eastern European',
     'North African and Middle Eastern',
     'Peoples of the Americas',
     'Sub-Saharan African',
     'Supplementary codes',
     'Not stated'],
    ['South-East Asian',
     'North-East Asian',
     'Southern and Central Asian']
]].sum(axis=1)

# Create a new column which sums the number of people with Asian ancestry
df_ancestry['asian_ancestry'] = df_ancestry.loc[idx[:], idx[['asian_1st_response', 'asian_2nd_response']]].sum(axis=1)

# Create a new column which sums the number of people who took part in this question, including 'Not stated'
df_ancestry['total_individuals'] = df_ancestry.loc[idx[:], idx[
    ['Oceanian',
     'North-West European',
     'Southern and Eastern European',
     'North African and Middle Eastern',
     'South-East Asian',
     'North-East Asian',
     'Southern and Central Asian',
     'Peoples of the Americas',
     'Sub-Saharan African',
     'Supplementary codes',
     'Not stated']
]].sum(axis=1)

# Create a new column which shows the proportion of population with Asian ancestry
df_ancestry['asian_proportion'] = df_ancestry['asian_ancestry'] / df_ancestry['total_individuals']

# Simplify and re-compose the dataframe with columns that we need
df_asian_ancestry = df_ancestry[['SSC (UR)', 'asian_1st_response', 'asian_2nd_response', 'asian_ancestry', 'total_individuals', 'asian_proportion']].copy()

# Flatten MultiIndex columns
df_asian_ancestry.columns = df_asian_ancestry.columns.get_level_values(0)

df_asian_ancestry.head()

SSC (UR)  asian_1st_response  asian_2nd_response  asian_ancestry  \
0           Abbeyard                   0                   0               0   
1  Abbotsford (Vic.)                1662                 176            1838   
2         Aberfeldie                 273                  60             333   
3          Aberfeldy                   0                   0               0   
4            Acheron                   0                   0               0   

   total_individuals  asian_proportion  
0                  0               NaN  
1               8167          0.225052  
2               3880          0.085825  
3                  0               NaN  
4                161          0.000000

We now have a dataframe showing the number and proportion of population with Asian ancestry. Next, we will filter the dataframe to keep the 41 suburbs only.

In [35]:
# Insert empty column 'suburb' into df_asian_ancestry
df_asian_ancestry.insert(1, 'suburb', np.nan)

# Put the 41 suburbs in the 'suburb' column
for suburb in suburb_list:
    for i in range(len(df_asian_ancestry)):
        if suburb == re.sub(' \(.*\)', '', df_asian_ancestry.loc[i, 'SSC (UR)']).upper():
            df_asian_ancestry.loc[i, 'suburb'] = suburb

# Filter the dataframe to keep data only for the 41 suburbs
df_asian_ancestry = df_asian_ancestry[df_asian_ancestry['suburb'].notna()]

# Reset index
df_asian_ancestry.reset_index(drop=True, inplace=True)

df_asian_ancestry.head()

SSC (UR)          suburb  asian_1st_response  asian_2nd_response  \
0   Abbotsford (Vic.)      ABBOTSFORD                1662                 176   
1  Albert Park (Vic.)     ALBERT PARK                 303                  80   
2          Ascot Vale      ASCOT VALE                1784                 216   
3    Brunswick (Vic.)       BRUNSWICK                2807                 425   
4      Brunswick East  BRUNSWICK EAST                1259                 208   

   asian_ancestry  total_individuals  asian_proportion  
0            1838               8167          0.225052  
1             383               6214          0.061635  
2            2000              14717          0.135897  
3            3232              24455          0.132161  
4            1467              11479          0.127799

In [36]:
df_asian_ancestry.shape

(41, 7)

So we now have df_asian_ancestry containing Asian ancestry data of the 41 suburbs.

## Methodology <a name="methodology"></a>

In this project we try to find an optimal suburb for opening an Asian supermarket in Melbourne, Australia. Such a suburb should have **high population**, **low supermarket to population ratio**, and **high proportion of population with Asian ancestry**. We will limit our analysis to 5 km radius from Melbourne city centre.

In data section, we have collected the following: boundaries of 41 suburbs within 5 km from Melbourne city centre, location information of every supermarket within the 41 suburbs (Foursquare API), population and Asian ancestry data of the 41 suburbs (2016 Census).

In analysis section, we will look at number of supermarkets, population, supermarket to population ratio, Asian ancestry proportion in each suburb. We will narrow down our choice to suburbs with sufficient population, then suburbs currently with low supermarket to population ratio, and lastly suburbs with high Asian ancestry population. This will ensure that there will be sufficient room for competition, and enough population to be our target customers.

## Analysis <a name="analysis"></a>

We will perform some exploratory analysis and derive some additional info from our raw data. Let's first count the number of supermarkets in each of 41 suburbs.

In [37]:
df_foursquare['suburb'].value_counts()

MELBOURNE          21
BRUNSWICK           7
SOUTHBANK           6
SOUTH MELBOURNE     6
DOCKLANDS           6
FITZROY             5
ABBOTSFORD          4
NORTHCOTE           4
HAWTHORN            4
TOORAK              3
PRAHRAN             3
FOOTSCRAY           3
ST KILDA            3
BRUNSWICK WEST      3
FLEMINGTON          3
SOUTH YARRA         3
RICHMOND            3
CREMORNE            2
KEW                 2
KENSINGTON          2
CARLTON NORTH       2
CARLTON             2
ASCOT VALE          1
FAIRFIELD           1
PORT MELBOURNE      1
FITZROY NORTH       1
NORTH MELBOURNE     1
PARKVILLE           1
COLLINGWOOD         1
MIDDLE PARK         1
WINDSOR             1
ALBERT PARK         1
BRUNSWICK EAST      1
Name: suburb, dtype: int64

We see that suburb Melbourne has the highest number of supermarkets, 21. Some of the 41 suburbs do not appear in this series, indicating no supermarkets within them. Let's visualise this series on map.

In [38]:
import branca

# Create map of Melbourne
map_supermarket = folium.Map(location=melbourne_city_centre, tiles='cartodbpositron', zoom_start=12)

# Add city centre marker to map
folium.Marker(location=melbourne_city_centre, tooltip=melbourne_city_centre).add_to(map_supermarket)

# Define colorscale
colorscale = branca.colormap.linear.YlGnBu_09.scale(0, 21)

supermarket_series = df_foursquare['suburb'].value_counts()

#  Define how color is generated according to style_function
def style_function(feature):
    supermarket = supermarket_series.get(feature['properties']['vic_loca_2'], None)
    return {'fillOpacity': 0.5, 'weight': 0.3, 'fillColor': '#black' if supermarket is None else colorscale(supermarket)}

# Add color to suburbs based on number of supermarkets
folium.GeoJson(
    suburbs_within_5km,
    name='supermarket',
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(['vic_loca_2'], labels=False)
).add_to(map_supermarket)

map_supermarket

The colorscale we used is yellow-green-blue. We can see that suburb Melbourne has color deep blue, indicating highest number of supermarkets among the 41 suburbs. Suburbs filled with color black indicates 0 supermarkets in them.

Let's look at population data of the 41 suburbs.

In [39]:
df_population.sort_values(by='Total_Persons_Persons', ascending=False)

SSC_CODE_2016    Census_Name_2016           suburb  Total_Persons_Persons
22      SSC21629           Melbourne        MELBOURNE                  47285
30      SSC22158     Richmond (Vic.)         RICHMOND                  27705
33      SSC22303         South Yarra      SOUTH YARRA                  25147
21      SSC21328          Kew (Vic.)              KEW                  24605
25      SSC21959           Northcote        NORTHCOTE                  24561
3       SSC20359    Brunswick (Vic.)        BRUNSWICK                  24473
19      SSC21143     Hawthorn (Vic.)         HAWTHORN                  23511
35      SSC22332     St Kilda (Vic.)         ST KILDA                  20230
34      SSC22304           Southbank        SOUTHBANK                  18709
7       SSC20492      Carlton (Vic.)          CARLTON                  18535
18      SSC20929           Footscray        FOOTSCRAY                  16345
27      SSC22095      Port Melbourne   PORT MELBOURNE                  16175
24      SSC21954     North Melbourne  NORTH MELBOURNE                  14940
2       SSC20074          Ascot Vale       ASCOT VALE                  14750
5       SSC20361      Brunswick West   BRUNSWICK WEST                  14159
28      SSC22106             Prahran          PRAHRAN                  12982
37      SSC22534              Toorak           TOORAK                  12909
16      SSC20919       Fitzroy North    FITZROY NORTH                  12339
4       SSC20360      Brunswick East   BRUNSWICK EAST                  11504
12      SSC20760           Docklands        DOCKLANDS                  10964
31      SSC22299     South Melbourne  SOUTH MELBOURNE                  10920
20      SSC21319   Kensington (Vic.)       KENSINGTON                  10812
15      SSC20918      Fitzroy (Vic.)          FITZROY                  10445
10      SSC20612  Collingwood (Vic.)      COLLINGWOOD                   8513
0       SSC20002   Abbotsford (Vic.)       ABBOTSFORD                   8184
17      SSC20923          Flemington       FLEMINGTON                   7719
26      SSC22026    Parkville (Vic.)        PARKVILLE                   7409
40      SSC22791      Windsor (Vic.)          WINDSOR                   7281
14      SSC20895    Fairfield (Vic.)        FAIRFIELD                   6558
9       SSC20571        Clifton Hill     CLIFTON HILL                   6341
8       SSC20493       Carlton North    CARLTON NORTH                   6300
1       SSC20017  Albert Park (Vic.)      ALBERT PARK                   6215
39      SSC22743      West Melbourne   WEST MELBOURNE                   5515
13      SSC20824      East Melbourne   EAST MELBOURNE                   4964
23      SSC21666  Middle Park (Vic.)      MIDDLE PARK                   4143
36      SSC22334       St Kilda West    ST KILDA WEST                   3162
38      SSC22559          Travancore       TRAVANCORE                   2480
29      SSC22110        Princes Hill     PRINCES HILL                   2126
11      SSC20665     Cremorne (Vic.)         CREMORNE                   2018
6       SSC20416             Burnley          BURNLEY                    769
32      SSC22302         South Wharf      SOUTH WHARF                    106

In [40]:
df_population.describe()

Total_Persons_Persons
count              41.000000
mean            12531.902439
std              9329.088487
min               106.000000
25%              6300.000000
50%             10920.000000
75%             16345.000000
max             47285.000000

Let's visualise the population data on map.

In [41]:
# Create map of Melbourne
map_population = folium.Map(location=melbourne_city_centre, tiles='cartodbpositron', zoom_start=12)

# Add city centre marker to map
folium.Marker(location=melbourne_city_centre, tooltip=melbourne_city_centre).add_to(map_population)

# Define colorscale
colorscale = branca.colormap.linear.YlGnBu_09.scale(0, 47285)

population_series = df_population.set_index('suburb')['Total_Persons_Persons']

#  Define how color is generated according to style_function
def style_function(feature):
    population = population_series.get(feature['properties']['vic_loca_2'], None)
    return {'fillOpacity': 0.5, 'weight': 0.3, 'fillColor': '#black' if population is None else colorscale(population)}

# Add color to suburbs based on number of supermarkets
folium.GeoJson(
    suburbs_within_5km,
    name='supermarket',
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(['vic_loca_2'], labels=False)
).add_to(map_population)

map_population

Again, we can see that suburb Melbourne has the highest population, followed by Richmond, South Yarra, Kew, Northcote, Brunswick.

We now know the number of supermarkets and population in each suburb; however, to look for suburbs which are not yet saturated with supermarkets, we need to look at supermarket to population ratio. Let's calculate this ratio.

In [42]:
ratio_list = []

# Append the empty ratio_list with calculated ratios, suburbs with 0 supermarkets will have a ratio of 0
for suburb in suburb_list:
    try:
        ratio_list.append(df_foursquare['suburb'].value_counts()[suburb] / df_population.set_index('suburb')['Total_Persons_Persons'][suburb])
    except:
        ratio_list.append(0)

# Create a new dataframe with suburbs and ratios
df_sp_ratio = pd.DataFrame({'suburb': suburb_list, 'supermarket_to_population_ratio': ratio_list})

df_sp_ratio.head()

suburb  supermarket_to_population_ratio
0       BURNLEY                         0.000000
1       WINDSOR                         0.000137
2  PRINCES HILL                         0.000000
3     DOCKLANDS                         0.000547
4  CLIFTON HILL                         0.000000

In [43]:
df_sp_ratio.shape

(41, 2)

In [44]:
df_sp_ratio.describe()

supermarket_to_population_ratio
count                        41.000000
mean                          0.000197
std                           0.000202
min                           0.000000
25%                           0.000068
50%                           0.000148
75%                           0.000241
max                           0.000991

Let's visualise the supermarket to population ratio data on map.

In [45]:
# Create map of Melbourne
map_sp_ratio = folium.Map(location=melbourne_city_centre, tiles='cartodbpositron', zoom_start=12)

# Add city centre marker to map
folium.Marker(location=melbourne_city_centre, tooltip=melbourne_city_centre).add_to(map_sp_ratio)

# Define colorscale
colorscale = branca.colormap.linear.YlGnBu_09.scale(0, 0.000991)

sp_ratio_series = df_sp_ratio.set_index('suburb')['supermarket_to_population_ratio']

#  Define how color is generated according to style_function
def style_function(feature):
    sp_ratio = sp_ratio_series.get(feature['properties']['vic_loca_2'], None)
    return {'fillOpacity': 0.5, 'weight': 0.3, 'fillColor': '#black' if sp_ratio is None else colorscale(sp_ratio)}

# Add color to suburbs based on supermarket to population ratio
folium.GeoJson(
    suburbs_within_5km,
    name='supermarket',
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(['vic_loca_2'], labels=False)
).add_to(map_sp_ratio)

map_sp_ratio

Suburbs with pale color indicate low supermarket to population ratio, which is desirable for opening new supermarkets.

Next, we will look at the Asian ancestry data.

In [46]:
df_asian_ancestry.sort_values(by='asian_proportion', ascending=False)

SSC (UR)           suburb  asian_1st_response  \
22           Melbourne        MELBOURNE               26471   
7       Carlton (Vic.)          CARLTON                9005   
12           Docklands        DOCKLANDS                5078   
34           Southbank        SOUTHBANK                7523   
38          Travancore       TRAVANCORE                 986   
18           Footscray        FOOTSCRAY                5655   
39      West Melbourne   WEST MELBOURNE                1819   
24     North Melbourne  NORTH MELBOURNE                4676   
26    Parkville (Vic.)        PARKVILLE                1824   
0    Abbotsford (Vic.)       ABBOTSFORD                1662   
19     Hawthorn (Vic.)         HAWTHORN                4737   
21          Kew (Vic.)              KEW                4901   
33         South Yarra      SOUTH YARRA                4576   
20   Kensington (Vic.)       KENSINGTON                1931   
17          Flemington       FLEMINGTON                1370   
30     Richmond (Vic.)         RICHMOND                4773   
32         South Wharf      SOUTH WHARF                  17   
10  Collingwood (Vic.)      COLLINGWOOD                1291   
31     South Melbourne  SOUTH MELBOURNE                1509   
5       Brunswick West   BRUNSWICK WEST                1849   
15      Fitzroy (Vic.)          FITZROY                1360   
37              Toorak           TOORAK                1679   
2           Ascot Vale       ASCOT VALE                1784   
3     Brunswick (Vic.)        BRUNSWICK                2807   
4       Brunswick East   BRUNSWICK EAST                1259   
40      Windsor (Vic.)          WINDSOR                 776   
28             Prahran          PRAHRAN                1281   
13      East Melbourne   EAST MELBOURNE                 477   
14    Fairfield (Vic.)        FAIRFIELD                 566   
35     St Kilda (Vic.)         ST KILDA                1799   
36       St Kilda West    ST KILDA WEST                 252   
25           Northcote        NORTHCOTE                1617   
6              Burnley          BURNLEY                  54   
8        Carlton North    CARLTON NORTH                 404   
16       Fitzroy North    FITZROY NORTH                 762   
29        Princes Hill     PRINCES HILL                 130   
9         Clifton Hill     CLIFTON HILL                 360   
27      Port Melbourne   PORT MELBOURNE                 976   
11     Cremorne (Vic.)         CREMORNE                  96   
1   Albert Park (Vic.)      ALBERT PARK                 303   
23  Middle Park (Vic.)      MIDDLE PARK                 159   

    asian_2nd_response  asian_ancestry  total_individuals  asian_proportion  
22                 851           27322              47264          0.578072  
7                  340            9345              18531          0.504290  
12                 182            5260              10953          0.480234  
34                 374            7897              18702          0.422254  
38                  34            1020               2448          0.416667  
18                 417            6072              16338          0.371649  
39                 131            1950               5506          0.354159  
24                 283            4959              14911          0.332573  
26                 157            1981               7408          0.267414  
0                  176            1838               8167          0.225052  
19                 476            5213              23485          0.221971  
21                 439            5340              24591          0.217153  
33                 494            5070              25159          0.201518  
20                 209            2140              10780          0.198516  
17                 140            1510               7704          0.196002  
30                 505            5278              27711          0.190466  
32                   0              17   

In [47]:
df_asian_ancestry.describe()

asian_1st_response  asian_2nd_response  asian_ancestry  \
count           41.000000           41.000000       41.000000   
mean          2696.439024          220.634146     2917.073171   
std           4363.025688          175.441836     4504.806868   
min             17.000000            0.000000       17.000000   
25%            566.000000          110.000000      682.000000   
50%           1509.000000          178.000000     1665.000000   
75%           2807.000000          301.000000     3232.000000   
max          26471.000000          851.000000    27322.000000   

       total_individuals  asian_proportion  
count          41.000000         41.000000  
mean        12522.682927          0.192468  
std          9331.003219          0.134619  
min            94.000000          0.051728  
25%          6280.000000          0.092269  
50%         10905.000000          0.147868  
75%         16338.000000          0.221971  
max         47264.000000          0.578072

Let's visualise the Asian ancestry proportion data on map.

In [48]:
# Create map of Melbourne
map_asian_proportion = folium.Map(location=melbourne_city_centre, tiles='cartodbpositron', zoom_start=12)

# Add city centre marker to map
folium.Marker(location=melbourne_city_centre, tooltip=melbourne_city_centre).add_to(map_asian_proportion)

# Define colorscale
colorscale = branca.colormap.linear.YlGnBu_09.scale(0, 0.578072)

asian_ancestry_series = df_asian_ancestry.set_index('suburb')['asian_proportion']

#  Define how color is generated according to style_function
def style_function(feature):
    asian_ancestry = asian_ancestry_series.get(feature['properties']['vic_loca_2'], None)
    return {'fillOpacity': 0.5, 'weight': 0.3, 'fillColor': '#black' if asian_ancestry is None else colorscale(asian_ancestry)}

# Add color to suburbs based on Asian ancestry proportion
folium.GeoJson(
    suburbs_within_5km,
    name='supermarket',
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(['vic_loca_2'], labels=False)
).add_to(map_asian_proportion)

map_asian_proportion

Again, suburb Melbourne has the highest Asian ancestry proportion, followed by suburbs in the north and northwest of Melbourne city centre.

Let's combine data of population, supermarket to population ratio, and Asian ancestry proportion together into one dataframe.

In [49]:
df_combined = df_population[['suburb', 'Total_Persons_Persons']].join(
    df_sp_ratio.set_index('suburb'), on='suburb').join(
    df_asian_ancestry[['suburb', 'asian_proportion']].set_index('suburb'), on='suburb'
)

df_combined.head()

suburb  Total_Persons_Persons  supermarket_to_population_ratio  \
0      ABBOTSFORD                   8184                         0.000489   
1     ALBERT PARK                   6215                         0.000161   
2      ASCOT VALE                  14750                         0.000068   
3       BRUNSWICK                  24473                         0.000286   
4  BRUNSWICK EAST                  11504                         0.000087   

   asian_proportion  
0          0.225052  
1          0.061635  
2          0.135897  
3          0.132161  
4          0.127799

In [50]:
df_combined.describe()

Total_Persons_Persons  supermarket_to_population_ratio  \
count              41.000000                        41.000000   
mean            12531.902439                         0.000197   
std              9329.088487                         0.000202   
min               106.000000                         0.000000   
25%              6300.000000                         0.000068   
50%             10920.000000                         0.000148   
75%             16345.000000                         0.000241   
max             47285.000000                         0.000991   

       asian_proportion  
count         41.000000  
mean           0.192468  
std            0.134619  
min            0.051728  
25%            0.092269  
50%            0.147868  
75%            0.221971  
max            0.578072

We will look for the best 5 suburbs to open an Asian supermarket based on the following:
* Population is equal to or higher than 10920, which is the median of the 41 suburbs
* Supermarket to population ratio is equal to or lower than 0.000148, which is the median of the 41 suburbs
* 5 suburbs with the highest Asian proportion after meeting the above 2 criteria

In [51]:
df_combined[(df_combined['Total_Persons_Persons']>=10920) & (df_combined['supermarket_to_population_ratio']<=0.000148)].sort_values(by='asian_proportion', ascending=False).head()

suburb  Total_Persons_Persons  supermarket_to_population_ratio  \
7           CARLTON                  18535                         0.000108   
24  NORTH MELBOURNE                  14940                         0.000067   
21              KEW                  24605                         0.000081   
33      SOUTH YARRA                  25147                         0.000119   
30         RICHMOND                  27705                         0.000108   

    asian_proportion  
7           0.504290  
24          0.332573  
21          0.217153  
33          0.201518  
30          0.190466

And here we have the best 5 suburbs: Carlton, North Melbourne, Kew, South Yarra, and Richmond.

## Results and Discussion <a name="results"></a>

Our analysis has picked Carlton, North Melbourne, Kew, South Yarra, and Richmond as the best 5 suburbs among 41 suburbs within 5 km of Melbourne city centre to open an Asian supermarket. These suburbs all have relatively high population, low supermarket to population ratio, and high Asian proportion.

It is worth noting that we chose the median to filter suburbs on population and supermarket to population ratio. These choices were rather arbitrary. If different values were chosen for filtering, our results would be different. How large is required of a population to sustain one supermarket? This can only be answered by further market researches.

It should also be noted that our analysis only took number of supermarkets within suburbs, without regarding their exact locations. For sure, people living in small suburbs do shop at supermarket in neighboring suburbs. Hence a more detailed analysis should take note of the exact locations of supermarkets and also locations where the population resides within a suburb.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify an optimal suburb to open an Asian supermarket in Melbourne, Australia. We used population, supermarket to population ratio, Asian ancestry proportion as selection criteria. While we have picked the best 5 suburbs for our project, the exact location to open the supermarket will require further market researches by the stakeholders. These researches will need to look at the exact locations of existing supermarkets and where population resides in the suburb.